## Overview:



In [66]:

import pandas as pd
import folium
from folium.plugins import MarkerCluster
import geopandas as gpd
from shapely.geometry import Point, LineString
from shapely import wkt

crs = 4386

In [67]:
# Load the data
basin_data = pd.read_csv('./data/basin_data.csv', sep = ',', index_col=0)

# Convert to a geoDataFrame
basin_data['geometry'] = basin_data['geometry'].apply(wkt.loads)
geodata = gpd.GeoDataFrame(basin_data, crs = crs)
geodata.head()

geometry   type  \
0  POLYGON ((-106.18172 36.02367, -106.18846 36.0...  basin   
1  LINESTRING (-106.12648 36.08426, -106.12558 36...   main   
2  LINESTRING (-106.12854 36.08506, -106.12800 36...   main   
3  LINESTRING (-106.13018 36.08646, -106.12919 36...   main   
4  LINESTRING (-106.14259 36.10938, -106.14271 36...   main   

                                    description  
0                               Basin boundary.  
1  The mainflow river upstream of USGS-08290000  
2  The mainflow river upstream of USGS-08290000  
3  The mainflow river upstream of USGS-08290000  
4  The mainflow river upstream of USGS-08290000

In [68]:
## Plot options

# Line widths
basin_linewidth = 2
mainstem_linewidth = 3
tributary_linewidth = 1

# Line colors
mainstem_color = '#0a4b6e'
tributary_color = '#5e9eab'
basin_color = '#213b4a'

# Point colors
usgs_color = '#2a6339'
nmwdi_color = '#70207a'
pourpoint_color = '#8f5e1a'

# Point sizes
usgs_size = 10
nmwdi_size = 10
pourpoint_size = 5

# Other options
fill_opacity = 0.85
popup_width = 300

# Combine options into a dictionary
plot_options = {
    'station':{'color': usgs_color,
               'size': usgs_size},
    'pourpoint': {'color': pourpoint_color,
                  'size': pourpoint_size},
    'nmwdi': {'color': nmwdi_color, 
              'size': nmwdi_size}
    }

In [69]:
# Initialize the map
start_coords = [36.5, -106.5]  
geomap = folium.Map(location = start_coords, 
                    zoom_start = 9.2,
                    tiles = 'cartodbpositron',
                    control_scale = True)

# Start feature groups for toggle functionality
basin_layer = folium.FeatureGroup(name = 'Basin Boundary', show=True)
usgs_layer = folium.FeatureGroup(name = 'USGS Gauges', show=True)
mainstem_layer = folium.FeatureGroup(name = 'Mainstem River', show=True)
tributary_layer = folium.FeatureGroup(name='Tributary Rivers', show=False)
pourpoint_layer = folium.FeatureGroup(name= 'HUC12 Pour Points', show=False)
nmwdi_layer = folium.FeatureGroup(name='NM Water Data Initiative Gauge', show=True)

## Add differ tiles (base maps)
folium.TileLayer('openstreetmap').add_to(geomap)
folium.TileLayer('stamenwatercolor').add_to(geomap)
folium.TileLayer('stamenterrain').add_to(geomap)

In [70]:
## Plotting Polygons and Lines

# Plot basin border
for i,r in geodata.loc[geodata['type'] == 'basin'].iterrows():

    geo_json = gpd.GeoSeries(r['geometry']).simplify(tolerance = 0.000001).to_json()
    geo_json = folium.GeoJson(data= geo_json,
                        style_function=lambda x: {'fillcolor': 'none',
                                                    'weight': basin_linewidth, 
                                                    'color': basin_color,
                                                    'opacity': 1,
                                                    'fill_opacity': 1,
                                                    'fill': False})
    folium.Popup(r.description,
                min_width = popup_width,
                max_width= popup_width).add_to(geo_json)
    geo_json.add_to(basin_layer)
    
# Add mainstem flowlines
for i,r in geodata.loc[geodata['type'] == 'main'].iterrows():
    
    geo_json = gpd.GeoSeries(r['geometry']).simplify(tolerance = 0.000001).to_json()
    geo_json = folium.GeoJson(data= geo_json,
                              style_function=lambda x: {'fillcolor': 'none',
                                                        'weight': mainstem_linewidth, 
                                                        'color': mainstem_color,
                                                        'opacity': 1,
                                                        'fill_opacity': 1,
                                                        'fill': False})
    folium.Popup(r.description,
                min_width = popup_width,
                max_width= popup_width).add_to(geo_json)
    geo_json.add_to(mainstem_layer)
    
    
# Add tributary flow lines
for i,r in geodata.loc[geodata['type'] == 'tributary'].iterrows():
    
    geo_json = gpd.GeoSeries(r['geometry']).simplify(tolerance = 0.000001).to_json()
    geo_json = folium.GeoJson(data= geo_json,
                              style_function=lambda x: {'fillcolor': 'none',
                                                        'weight': tributary_linewidth, 
                                                        'color': tributary_color,
                                                        'opacity': 1,
                                                        'fill_opacity': 1,
                                                        'fill': False})
    folium.Popup(r.description,
                min_width = popup_width,
                max_width= popup_width).add_to(geo_json)
    geo_json.add_to(tributary_layer)

In [71]:
## Plotting point data

plot_types = ['station', 'nmwdi', 'pourpoint']
plot_layers = [usgs_layer, nmwdi_layer, pourpoint_layer]

for i, feature_type in enumerate(plot_types):

    map_layer = plot_layers[i]
    
    for _, point in geodata.loc[geodata['type'] == feature_type].iterrows():
        
        coords = [point.geometry.y, point.geometry.x]
        
        textbox = folium.Popup(point.description,
                             min_width= popup_width,
                             max_width= popup_width)
 
        folium.CircleMarker(coords,
                            popup= textbox,
                            fill_color = plot_options[feature_type]['color'],
                            fill = True,
                            fill_opacity = fill_opacity,
                            radius= plot_options[feature_type]['size'],
                            color = plot_options[feature_type]['color']).add_to(map_layer)
 


In [72]:
basin_layer.add_to(geomap)
usgs_layer.add_to(geomap)
mainstem_layer.add_to(geomap)
tributary_layer.add_to(geomap)
pourpoint_layer.add_to(geomap)
nmwdi_layer.add_to(geomap)

folium.LayerControl().add_to(geomap)

geomap.save("basin_map.html")
geomap